# Install

In [ ]:
%pip install uv

In [ ]:
!uv pip install dagshub setuptools accelerate toml torch torchvision transformers mlflow datasets ipywidgets python-dotenv evaluate

# Setup

In [1]:
import os
import toml
import torch
import mlflow
import dagshub
import datasets
import evaluate
from dotenv import load_dotenv
from torchvision.transforms import v2
from transformers import AutoImageProcessor, AutoModelForImageClassification, TrainingArguments, Trainer

ENV_PATH = "/Users/andrewmayes/Openclassroom/CanineNet/.env"
CONFIG_PATH = "/Users/andrewmayes/Openclassroom/CanineNet/code/config.toml"
CONFIG = toml.load(CONFIG_PATH)

load_dotenv(ENV_PATH)

dagshub.init(repo_name=os.environ['MLFLOW_TRACKING_PROJECTNAME'], repo_owner=os.environ['MLFLOW_TRACKING_USERNAME'], mlflow=True, dvc=True)

os.environ['MLFLOW_TRACKING_USERNAME'] = "amaye15"

mlflow.set_tracking_uri(f'https://dagshub.com/' + os.environ['MLFLOW_TRACKING_USERNAME']
                         + '/' + os.environ['MLFLOW_TRACKING_PROJECTNAME'] + '.mlflow')

CREATE_DATASET = True
ORIGINAL_DATASET = "Alanox/stanford-dogs"
MODIFIED_DATASET = "amaye15/stanford-dogs"
REMOVE_COLUMNS = ["name", "annotations"]
RENAME_COLUMNS = {"image":"pixel_values", "target":"label"}
SPLIT = 0.2

METRICS = ["accuracy", "f1", "precision", "recall"]
# MODELS = 'google/vit-base-patch16-224'
# MODELS = "google/siglip-base-patch16-224"



Initialized MLflow to track repo "amaye15/CanineNet"

Repository amaye15/CanineNet initialized!

# Dataset

In [2]:
if CREATE_DATASET:
    ds = datasets.load_dataset(ORIGINAL_DATASET, token=os.getenv("HF_TOKEN"), split="full", trust_remote_code=True)
    ds = ds.remove_columns(REMOVE_COLUMNS).rename_columns(RENAME_COLUMNS)

    labels = ds.select_columns("label").to_pandas().sort_values("label").get("label").unique().tolist()
    numbers = range(len(labels))
    label2int = dict(zip(labels, numbers))
    int2label = dict(zip(numbers, labels))

    for key, val in label2int.items():
        print(f"{key}: {val}")

    ds = ds.class_encode_column("label")
    ds = ds.align_labels_with_mapping(label2int, "label")

    ds = ds.train_test_split(test_size=SPLIT, stratify_by_column = "label")
    #ds.push_to_hub(MODIFIED_DATASET, token=os.getenv("HF_TOKEN"))

    CONFIG["label2int"] = str(label2int)
    CONFIG["int2label"] = str(int2label)

    # with open("output.toml", "w") as toml_file:
    #     toml.dump(toml.dumps(CONFIG), toml_file)

    #ds = datasets.load_dataset(MODIFIED_DATASET, token=os.getenv("HF_TOKEN"), trust_remote_code=True, streaming=True)

Affenpinscher: 0
Afghan Hound: 1
African Hunting Dog: 2
Airedale: 3
American Staffordshire Terrier: 4
Appenzeller: 5
Australian Terrier: 6
Basenji: 7
Basset: 8
Beagle: 9
Bedlington Terrier: 10
Bernese Mountain Dog: 11
Black And Tan Coonhound: 12
Blenheim Spaniel: 13
Bloodhound: 14
Bluetick: 15
Border Collie: 16
Border Terrier: 17
Borzoi: 18
Boston Bull: 19
Bouvier Des Flandres: 20
Boxer: 21
Brabancon Griffon: 22
Briard: 23
Brittany Spaniel: 24
Bull Mastiff: 25
Cairn: 26
Cardigan: 27
Chesapeake Bay Retriever: 28
Chihuahua: 29
Chow: 30
Clumber: 31
Cocker Spaniel: 32
Collie: 33
Curly Coated Retriever: 34
Dandie Dinmont: 35
Dhole: 36
Dingo: 37
Doberman: 38
English Foxhound: 39
English Setter: 40
English Springer: 41
Entlebucher: 42
Eskimo Dog: 43
Flat Coated Retriever: 44
French Bulldog: 45
German Shepherd: 46
German Short Haired Pointer: 47
Giant Schnauzer: 48
Golden Retriever: 49
Gordon Setter: 50
Great Dane: 51
Great Pyrenees: 52
Greater Swiss Mountain Dog: 53
Groenendael: 54
Ibizan Hou

In [3]:
metrics = {metric: evaluate.load(metric) for metric in METRICS}


# for lr in [5e-3, 5e-4, 5e-5]: # 5e-5
#     for batch in [64]: # 32
#         for model_name in ["google/vit-base-patch16-224", "microsoft/swinv2-base-patch4-window16-256", "google/siglip-base-patch16-224"]: # "facebook/dinov2-base"

lr = 5e-4
batch = 32
model_name = "microsoft/swinv2-base-patch4-window16-256"

image_processor = AutoImageProcessor.from_pretrained(model_name)
model = AutoModelForImageClassification.from_pretrained(
model_name,
num_labels=len(label2int),
id2label=int2label,
label2id=label2int,
ignore_mismatched_sizes=True,
)

# Then, in your transformations:
def train_transform(examples, num_ops=10, magnitude=9, num_magnitude_bins=31):

    transformation = v2.Compose(
        [
            v2.RandAugment(
                num_ops=num_ops,
                magnitude=magnitude,
                num_magnitude_bins=num_magnitude_bins,
            )
        ]
    )
    # Ensure each image has three dimensions (in this case, ensure it's RGB)
    examples["pixel_values"] = [
        image.convert("RGB") for image in examples["pixel_values"]
    ]
    # Apply transformations
    examples["pixel_values"] = [
        image_processor(transformation(image), return_tensors="pt")[
            "pixel_values"
        ].squeeze()
        for image in examples["pixel_values"]
    ]
    return examples


def test_transform(examples):
    # Ensure each image is RGB
    examples["pixel_values"] = [
        image.convert("RGB") for image in examples["pixel_values"]
    ]
    # Apply processing
    examples["pixel_values"] = [
        image_processor(image, return_tensors="pt")["pixel_values"].squeeze()
        for image in examples["pixel_values"]
    ]
    return examples


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    # predictions = np.argmax(logits, axis=-1)
    results = {}
    for key, val in metrics.items():
        if "accuracy" == key:
            result = next(
                iter(val.compute(predictions=predictions, references=labels).items())
            )
        if "accuracy" != key:
            result = next(
                iter(
                    val.compute(
                        predictions=predictions, references=labels, average="macro"
                    ).items()
                )
            )
        results[result[0]] = result[1]
    return results


def collate_fn(examples):
    pixel_values = torch.stack([example["pixel_values"] for example in examples])
    labels = torch.tensor([example["label"] for example in examples])
    return {"pixel_values": pixel_values, "labels": labels}


def preprocess_logits_for_metrics(logits, labels):
    """
    Original Trainer may have a memory leak.
    This is a workaround to avoid storing too many tensors that are not needed.
    """
    pred_ids = torch.argmax(logits, dim=-1)
    return pred_ids

ds["train"].set_transform(train_transform)
ds["test"].set_transform(test_transform)

training_args = TrainingArguments(**CONFIG["training_args"])
training_args.per_device_train_batch_size = batch
training_args.per_device_eval_batch_size = batch
training_args.hub_model_id = f"amaye15/{model_name.replace('/','-')}-batch{batch}-lr{lr}-standford-dogs"

mlflow.start_run(run_name=f"{model_name.replace('/','-')}-batch{batch}-lr{lr}")

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=ds["train"],
    eval_dataset=ds["test"],
    tokenizer=image_processor,
    data_collator=collate_fn,
    compute_metrics=compute_metrics,
    # callbacks=[early_stopping_callback],
    preprocess_logits_for_metrics=preprocess_logits_for_metrics,
)

# Train the model
trainer.train()

trainer.push_to_hub()

mlflow.end_run()

/Users/andrewmayes/Openclassroom/CanineNet/env/lib/python3.12/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Could not find image processor class in the image processor config or the model config. Loading based on pattern matching with the model's feature extractor configuration. Please open a PR/issue to update `preprocessor_config.json` to use `image_processor_type` instead of `feature_extractor_type`. This warning will be removed in v4.40.
Some weights of Swinv2ForImageClassification were not initialized from the model checkpoint at microsoft/swinv2-base-patch4-window16-256 and are newly initialized because the shapes did not match:
- classifier.weight: found shape torch.Size([1000, 1024]) in the checkpoint and torch.Size([120, 1024]) in the model instantiated
- classifier.bi

  0%|          | 0/1000 [00:00<?, ?it/s]

/Users/andrewmayes/Openclassroom/CanineNet/env/lib/python3.12/site-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


{'loss': 4.7518, 'grad_norm': 9.390625953674316, 'learning_rate': 4.9500000000000004e-05, 'epoch': 0.08}


  0%|          | 0/129 [00:00<?, ?it/s]

...

/Users/andrewmayes/Openclassroom/CanineNet/env/lib/python3.12/site-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


{'loss': 0.3549, 'grad_norm': 26.349733352661133, 'learning_rate': 2.9e-05, 'epoch': 3.26}


  0%|          | 0/129 [00:00<?, ?it/s]

{'eval_loss': 0.19598565995693207, 'eval_accuracy': 0.9390184645286687, 'eval_f1': 0.936971760890017, 'eval_precision': 0.9409831330401592, 'eval_recall': 0.938080489222113, 'eval_runtime': 118.5544, 'eval_samples_per_second': 34.718, 'eval_steps_per_second': 1.088, 'epoch': 3.26}


/Users/andrewmayes/Openclassroom/CanineNet/env/lib/python3.12/site-packages/torch/utils/checkpoint.py:464: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  warnings.warn(


In [ ]:
mlflow.end_run()

In [ ]:
# training_args = TrainingArguments(**CONFIG["training_args"])

# image_processor = AutoImageProcessor.from_pretrained(MODELS)
# model = AutoModelForImageClassification.from_pretrained(
# MODELS,
# num_labels=len(CONFIG["label2int"]),
# id2label=CONFIG["label2int"],
# label2id=CONFIG["int2label"],
# ignore_mismatched_sizes=True,
# )


# training_args = TrainingArguments(**CONFIG["training_args"])

# trainer = Trainer(
#     model=model,
#     args=training_args,
#     train_dataset=ds["train"],
#     eval_dataset=ds["test"],
#     tokenizer=image_processor,
#     data_collator=collate_fn,
#     compute_metrics=compute_metrics,
#     # callbacks=[early_stopping_callback],
#     preprocess_logits_for_metrics=preprocess_logits_for_metrics,
# )

# # Train the model
# trainer.train()

# mlflow.end_run()